# nepberta

In [ ]:
%cd /content/drive/MyDrive/Research/datasets/hf_datasets

/content/drive/MyDrive/Research/datasets/hf_datasets


In [ ]:
# Probably should `clean_data(new_crawled_data)` before merging `new_crawled_data.csv` and previous`cleaned_data.csv`

from bs4 import BeautifulSoup
import csv
import json
import re
import string
import pandas as pd

from drive.MyDrive.Research.datasets.scrapy_engine.code.load_data import load_data
class CleanData:
    def __init__(self):
        pass
        # return text
    # Example of removing HTML tags
    def clean_html(self, text):
        '''
        # HTML Tag Removal:
        * removes html tags like: <h1>
        * Removes css or js code inside <style> and <script> tags
        '''
        soup = BeautifulSoup(text, "lxml")

        # Remove all <script> and <style> tags
        for script_or_style in soup(['script', 'style']):
            script_or_style.decompose()

        # Get text from the modified HTML
        text = soup.get_text(separator=' ', strip=True)
        # print(text)

        return text

    def convert_to_devanagari_digits(self, input_string):
        # Function to convert 0-9 to ० - ९
        # i.e. Mapping of ASCII digits to Devanagari digits
        devanagari_digits = {
            '0': '०',
            '1': '१',
            '2': '२',
            '3': '३',
            '4': '४',
            '5': '५',
            '6': '६',
            '7': '७',
            '8': '८',
            '9': '९'
        }
        # Convert each digit in the input string
        result = ''.join(devanagari_digits[char] if char in devanagari_digits else char for char in input_string)
        return result

    def remove_non_devanagari_characters(self, text, keep_special_characters=True):
        '''
            # Function to find nepali sequences.
            * keep punctuations if they occur between devanagari characters.
            * Remove punctuation if previous character is not devanagari.
            # Examples
            texts = [
                "उनले दुहेको दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे। \"hi there\". what is your name? उनले दुहेको दूध",
                "\"hi there. \"उनले दुहेको\" दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे। hi there. what is your name? उनले दुहेको दूध\"",
                "name? उनले दुहेको दूध\""    #output: (last quatation, name?) should be ignored
                ]

            for text in texts:
                removed = remove_non_devanagari_characters(text)
                print(f'text: {text}, \nclen: {removed}\n\n')


            # output
            text: उनले दुहेको दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे। "hi there". what is your name? उनले दुहेको दूध,
            clen: उनले दुहेको दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे।             उनले दुहेको दूध


            text: "hi there. "उनले दुहेको" दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे। hi there. what is your name? उनले दुहेको दूध",
            clen:    "उनले दुहेको दूध बेच्नका लागि बजार असाध्यै सानो थियो त्यसैले उनले चीज बनाउने विचार गरे।             उनले दुहेको दूध"


            text: name? उनले दुहेको दूध",
            clen:  उनले दुहेको दूध"
        '''
        def is_devanagari(char):
            pattern=r'[ऀ-ॿ]'
            return bool(re.match(pattern, char))

        if not keep_special_characters:
            return re.sub(r"[^ऀ-ॿ ]", " ", text)

        sequences = []
        sequence = ''
        punctuation_symbols = string.punctuation    # '!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'
        prefix_punctuations = '\"\'(<[{'
        index=0
        while index < len(text):
            char = text[index]
            if is_devanagari(char) or char == ' ':
                # Character is devanagari
                sequence += char
            elif char in punctuation_symbols:
                # Character is punctuation
                if sequence != '':
                    if (len(text) > index+1) and not is_devanagari(text[index+1]):
                        # e.g. गरे। "hi there" : skip quotation before hi
                        pass
                    else:
                        sequence += char    # Sequence is no empty. i.e. previous char/sequence was devanagari otherwise ignore  punctuation
                elif (len(text) > index+1) and is_devanagari(text[index+1]):
                    # preserve prefix punctuations in devanagari. e.g. """there. \"उनले "": preserve double-quotation before उनले
                    sequence = char + text[index+1]
                    index += 1  # another 1 is added at the end
            else:
                if sequence:
                    sequences.append(sequence)
                    sequence = ''   # Reset sequence
            index += 1

            # print(f'{sequences}\n{sequence}\n{char}{is_devanagari(char)}\n\n')
        if sequence:    # last sequence
            sequences.append(sequence)
        return ' '.join(sequences)
        # Example of using regex for special character removal

    def normalize_data(self, text):
      '''
        * Standerize special characters
        * e.g. convert different types of quotes to standard quotes
      '''
      characters_to_replace = {
        '₹': 'रु',
        'ʻ': "'",
        'ː': ':',
        '？': '?',
        '‟': '"',
        '“' : '"',
        '”': '"',
        '`': "'",
        '৷': '।',
        'ˈ': "'",
        '՛': "'",
        'ǃ': '!',
        '（': '(',
        '：': ':',
        'ˍ': '_',
        '﹣': '-',
        '״': '"',
        'ꞌ': "'",
        '₋': '-',
        '％': '%',
        '꞉': ':',
        '‵': "'"
      }
      # Replace each character in the dictionary with its corresponding standard character
      for char, replacement in characters_to_replace.items():
          text = text.replace(char, replacement)

      return text

    def clean_data(self, text):
        # Remove HTML tags
        text = self.clean_html(text)

        # Normalize some characters
        text = self.normalize_data(text)

        # Convert convert 0-9 to ० - ९
        text = self.convert_to_devanagari_digits(text)

        text = self.remove_non_devanagari_characters(text, keep_special_characters=True)
        # text = text.lower() # No lower characters in devanagari

        # Replace one or more spaces with a single space
        text = re.sub(r'\s+', ' ', text).strip()

        return text

# Clean data and save to 'cleaned_data'
data_cleaner = CleanData()

# if __name__=="__main__":
#     # Assuming `data` is your raw dataset
#     data0 = ["<html><h1>Hi there</h1><style>color:red</style><script>console.log('hello world');</script>Example text</html>", "<div>Another example with special chars: !@#</div>"]
#     data = ['<html><h1>सुर्खेत र    </h1><style> जुम्लामा बाहेक </style><script>console.log("कर्णालीका अरू जिल्लामा");</script>      कर्णालीका अरू जिल्लामा शिशुका लागि आवश्यक एनआईसीयू सेवा नै उपलब्ध छैन।', 'नेपालले करिब एक महिना अघि नै औपचारिक पत्र पठाएर जीबी राईलाई स्वदेश फर्काइदिन गरेको आग्रहबारे मलेशियाले कुनै औपचारिक जबाफ दिएको छैन।', '2024 बीबीसी। अन्य वेबसाइटका सामग्रीहरूका लागि बीबीसी जिम्मेवार छैन।', 'संसदीय छानबिन समिति गठन नभएसम्म संसद्\u200cको कारबाही अघि बढ्न नदिने प्रतिपक्षी दलको अडानका कारण यसअघिको संसद् अधिवेशनको अन्त्यतिरका कामकारबाही प्रभावित भएका थिए।', 'भारतमा पनि भेपमा प्रतिबन्ध लगाइएको छ तर स्थानीय सञ्चार माध्यमका अनुसार यो व्यवस्था प्रभावकारी रूपमा कार्यान्वयन भएको छैन।', 'इजरेलले रफाहमा आक्रमण गर्न सक्ने आशङ्काका बीच अमेरिकाले गत साता इजरेललाई उपलब्ध गराउन लागेको हजारौँ बमको ढुवानी रोकिदिएको खुलासा भएको छ।', 'शुक्रवारको प्रयत्न सफल भएमा अन्तर्राष्ट्रिय अन्तरिक्ष स्टेशनतिर र बाट उडान गर्ने बोइङ दोस्रो निजी कम्पनी बन्नेछ। अहिलेसम्म इलोन मस्कको स्पेस एक्सले त्यस्तो काम गर्दै आएको छ।', 'हिरादेवी खतिवडाले दैनिक परामर्श दिनेहरूमा जबरजस्ती करणी, यौन दुर्व्यवहार लगायतका घटनाका पीडितहरू हुने गर्छन्।', 'युक्रेनी सेक्युरिटी सर्भिसका अनुसार गिरफ्तार गरिएका दुईजना कर्णेलले जेलेन्स्कीका अङ्गरक्षकहरूमध्ये त्यस्ता व्यक्तिको खोजी गरिरहेका थिए जो उनको अपहरण तथा हत्या गर्नका निम्ति इच्छुक होऊन्।', 'आधिकारिक रूपमा पुटिनले मार्चमा भएको राष्ट्रपतीय चुनावमा ८७ प्रतिशतभन्दा धेरै मत हासिल गरेका थिए। उक्त चुनावमा उनले गम्भीर प्रतिद्वन्दीको सामना गर्नुपरेको थिएन, न उक्त चुनावलाई धेरैले स्वतन्त्र र निष्पक्ष चुनावका रूपमा हेरेका थिए।', 'नेपालका ग्रामीण भेगमा विगतमा पाइने गरेका काठका पुराना ठेकीहरू अचेल नपाइने गरेका मानिसहरू बताउँछन्। आखिर कहाँ जादै छन् सारा ठेकीहरू?', 'चीनको अर्थतन्त्र सोचेभन्दा तीव्र गतिमा विकसित भए पनि यसका अगाडि विभिन्न सङ्कट रहेकाले \nमहिलाहरू घरखर्च धान्न बचत बढाउन चाहन्छन्।', "चार वर्षअघि जारी नेपालको पछिल्लो नक्सालाई अन्तर्राष्ट्रिय मान्यता दिलाउन उल्लेख्य प्रगति नभएको अवस्थामा सरकारको यो निर्णय 'लोकप्रियताका लागि मात्रै गरिएको' कतिपय विज्ञहरूको टिप्पणी छ।", 'जङ्गलमा कुनै प्राणीले औषधीय वनस्पति प्रयोग गरेर चोटपटकको उपचार गरेको यो पहिलो रेकर्ड हो। ', ' ', 'टिकटकले अमेरिकाले प्रतिबन्ध पुष्टि गर्न “अनुमानका आधारमा चिन्ता” व्यक्त गरेको आरोप लगाउँदै उक्त कदम रोक्न अदालतसँग माग गरेको छ।', "पुरातत्त्वसम्बन्धी विशेषज्ञ चित्रकारहरूले सयौँ टुक्राहरू जोडेर बनाइएको खप्परका आधारमा 'नीयान्डर्टाल' महिलाको थ्री-डी मोडल बनाएका छन्। ", 'प्री-मनसुनको समयमा नेपालमा चट्याङ र हावाहुरीका घटनाहरू धेरै हुने गरेको विज्ञहरू बताउँछन्।', 'त्रिसट्ठी वर्षीया चर्चित कलाकारले क्यान्सरविरुद्ध आफ्नो सङ्घर्ष र रङ्गमञ्च एवं सामाजिक सञ्जालमार्फत् आफ्नो यात्राबारे जनचेतना जगाउने निर्णयबारे बीबीसीसँग कुराकानी गरेकी छन्।', 'आस्ट्राजेनेका खोपले कोभिड महामारीका क्रममा लाखौं मनिसहरूको ज्यान बचाएको विश्वास गरिन्छ, तर सँगसँगै यसले केही दुर्लभ रक्तजन्य घातक समस्या पनि निम्त्याएको बताइन्छ। ', 'गत वर्ष अर्थात् सन् २०२३ मा २० हजार जनाभन्दा बढी नेपाली कोरिया गएका थिए। कोरियामा अहिले नेपाली कामदारको सङ्ख्या ५५ हजार जनाभन्दा धेरै रहेको त्यहाँस्थित नेपाली दूतावासले जनाएको छ।', 'एमालेका हिक्मत कार्की मुख्यमन्त्री नियुक्त भएको दिन नै त्यसविरुद्ध मुद्दा लिएर कांग्रेसका केदार कार्की सर्वोच्च अदालत पुगेका छन्।', "महत्त्वाकाङ्क्षी 'नीअम' परियोजनाअन्तर्गत 'द लाइन' मरुभूमि सहरका लागि जग्गा खाली गर्ने काममा घातक बल प्रयोग गर्न साउदी अरबका अधिकारीहरूले अनुमति दिएको एक भूतपूर्व गुप्तचर अधिकारीले दाबी गरेका छन्।\n", 'कडा कार्य संस्कृति प्रोत्साहन गर्ने टिप्पणीलाई लिएर चिनियाँ प्रविधि कम्पनीकी जनसम्पर्क अधिकारीले किन माफी माग्नु पर्\u200dयो।', "केन्द्रमा गत फागुनमा सत्ता समीकरण परिवर्तन भएसँगै त्यसको प्रभाव प्रदेशहरूमा परिरहेको देखिएका बेला जसपा विभाजनले विशेषगरी मधेश प्रदेश सरकार 'ढल्न सक्ने' अनुमानहरू पनि गरिएका छन्।", 'अदालतले उनलाई चुनाव प्रचारप्रसार गर्न कुनै खालको रोक नलगाएको र आदेशमा उनले के गर्न पाउने वा नपाउने भन्ने कुनै विषयबारे उल्लेख नगरिएको पनि केजरीवालका वकिलले बताए।', 'इजरेली प्रधानमन्त्रीले गाजाको रफाहमा पूर्ण स्तरको आक्रमणलाई अनुमति दिएको खण्डमा हतियारको आपूर्ति रोक्न सकिने अमेरिकी चेतावनीलगत्तै बेन्जमिन नेतन्याहुले इजरेल "एक्लै खडा हुन सक्ने" प्रतिक्रिया दिएका छन्।', 'ब्रजिलको रिओ ग्रान्डी डु सुल प्रान्तमा आएको बाढी र पहिरोका कारण धनजनको ठूलो क्षति भएको छ।', 'खासगरी प्रधानमन्त्री, मुख्यमन्त्री एवं प्रदेश प्रमुख परिवर्तन भइरहने अनि मनपरी ढङ्गले आफू अनुकूलका व्यक्तिका तस्बिर राख्दा त्यसको आर्थिकभार राज्यकोषमा पर्ने गरेको जानकारहरू बताउँछन्।', 'नेपाली कांग्रेसले गृहमन्त्री रवि लामिछाने सहकारी ठगीमा संलग्न भएको विवरण सञ्चारमाध्यममा आइरहेको भन्दै उनीमाथि पनि छानबिन हुने गरी संसदीय समिति गठन गरिनुपर्ने अडानमा छ। ', 'हजारौँ आप्रवासीहरूलाई तस्करी गरी यूके पुर्\u200dयाएका स्करपीअन उपनामले चर्चित बार्जान बीबीसीको एउटा अनुसन्धानपछि पक्राउ गरेका छन्। ', 'अमेरिकाका पूर्वराष्ट्रपति डोनल्ड ट्रम्पविरुद्ध परेको मुद्दामा उनका पूर्ववकिल माइकल कोएनले ट्रम्पविरुद्ध बयान दिएका छन्। उनले के भने र उनको बयान किन महत्त्वपूर्ण छ?', 'नेपालमा जेठ १५ गते बजेट ल्याउने नियम छ। त्यसअघि संसद्\u200cमा नीति तथा कार्यक्रम प्रस्तुत हुन्छ। यसपालि मङ्गलवार संसद्को दुवै सदनको संयुक्त बैठक बस्दैछ र त्यसमा राष्ट्रपति रामचन्द्र पौडेलले नीति तथा कार्यक्रम प्रस्तुत गर्ने कार्यक्रम तय भएको छ।', 'उत्तर कोरियाको एउटा प्रान्तमा मानिसहरू भोकभोकै मर्न थालेको सुनेपछि देश छाडेर दक्षिण कोरियामा शरण लिन पुगेका यी व्यक्तिले सन् २०१५ देखि बोतलमा अन्य चिजसँगै चामल भरेर पठाउन थालेका हुन्।\n', "पिनाइल क्यान्सर भनिने पुरुषहरूमा लिङ्गको क्यान्सरका एकजना बिरामी जोआओ भन्छन्, रोगको निदान भएपछि लिङ्ग काटेर हटाउनुपर्ने अवस्थाबाट उनी 'निकै आत्तिएका' थिए।", 'सर्वोच्च अदालतको संवैधानिक इजलासको फैसलाको पूर्णपाठमा हदबन्दीभन्दा बढी भएको जग्गा बाँझो राखिएको भेटिए सरकारका नाममा ल्याउन समेत भनिएको छ।', 'इन्टरनेटमा बालबालिकाले कलिलै उमेरमा पहुँच पाउँदा उनीहरू गम्भीर जोखिमको नजिक पुगेको विशेषज्ञहरूले बताएका छन्। ती जोखिमको रोकथामका लागि तपाईँहामी के गर्न सक्छौँ?', 'मृत्यु सन्निकट हुँदा मानिसहरूले गर्ने अनुभूतिबारे डा क्रिस्टोफर केरले अध्ययन गरेका छन्। त्यस्ता मानिसहरूले अन्तिम समयमा अनुभव गर्ने दृश्य र तिनको अर्थबारे उनले कुरा गरेका छन्।', "आत्मसम्मान कम भएका व्यक्तिमा  'कम्प्लिमेन्ट' अर्थात प्रशंसाले चिन्ता बढाउन सक्छ किनभने उनीहरूको स्वधारणामा त्यसरी भएको तारिफले चुनौती दिन सक्छ। ", 'सन् २०२२ मा जोन म्याकफललाई शारीरिक अपाङ्गता भएका प्रथम अन्तरिक्षयात्रीको उम्मेदवारका रूपमा चयन गरिएको थियो। ', "थाईल्यान्डमा 'लीज म्याजस्टी' कानुनले राजतन्त्रको आलोचना गर्न प्रतिबन्ध लगाएको छ। राजतन्त्रको संरक्षणका लागि बनाइएको त्यस्तो कानुनलाई विश्वकै कठोर कानुनमध्ये मानिन्छ।", "हजारौँ आप्रवासीहरूलाई तस्करी गरी यूके पुर्\u200dयाएका 'स्कोर्पिअन' उपनामले चर्चित बर्जान मजिद बीबीसीको एउटा अनुसन्धानपछि इराकमा पक्राउ परेका छन्। ", 'नयाँ नोट छपाइमा जानुअघि अन्तर्राष्ट्रिय बोलकबोलसहितका कतिपय कानुनी प्रक्रियाहरू पूरा गर्नुपर्ने अधिकारीहरू बताउँछन्। ', 'अमेरिका, चीन र भारतले चन्द्रमामा मानव पठाउने योजना सार्वजनिक गरेका छन्। अन्तरिक्ष अभियानमा यी देशले किन अर्बौँ डलर लगानी गरेका हुन् र उनीहरूको अपेक्षा के छ?', 'जबरजस्ती करणी मुद्दामा उच्च अदालत पाटनले सफाइ दिएको केही घण्टापछि नेपाल क्रिकेट सङ्घ क्यानको निर्णय सार्वजनिक भएको हो।', ' प्रधानमन्त्रीको टाउको र छातीमा गोली लागेको देखिएको थियो। प्रधानमन्त्रीका सुरक्षाकर्मीमध्ये तीन जनाले उनको उद्धार गरी कारभित्र लगेका थिए।', 'मसला उत्पादन र निर्यातमा भारतको वर्चस्व छ। तर विभिन्न देशमा भारतीय मसलाको गुणस्तरबारे प्रश्न उठेको छ।', 'हीरामन्डीमा प्रमुख भूमिका रहेको मल्लिका जानको अभिनय गरेर फिल्म क्षेत्रमा वाहवाही पाइरहेकी मनीषा कोइरालाले बलुवुडकी चर्चित कलाकार रेखाले आफ्नो प्रशंसा गरेको सुन्दा आँशु आएको बताएकी छन्। रेखाले हीरामन्डी हेरेपछि मनीषालाई के भनिन् र उनको आँखा रसाए?', "'लेडी बुशरा' नामले चिनिने अमिर डीन यूकेका सर्वाधिक चर्चित 'ड्र्याग कलाकार'मध्ये एक हुन्।", "साउदी अरबलाई आधुनिक बनाउने युवराज मोहम्मद बिन सलमानको चाहनाअनुसार 'नीअम' परियोजना बनाउन लागिएको हो। \n\n", 'कृषि जनशक्तिको चरम अभावमाझ राष्ट्रपतिले घोषणा गरेको महत्त्वाकाङ्क्षी कृषिमा लगानी दशक कार्यान्वयनमा नआउँदै गम्भीर प्रश्नहरू तेर्सिएका छन्।', 'युक्रेनमा जारी युद्धमा रुसलाई सघाएको आरोप चीनलाई लागेकै बेला भ्लादिमिर पुटिनले फेरि बेइजिङ भ्रमणमा पुगेका छन्।', 'भारतमा निर्वाचनका बेला डीपफेक र एआईबाट सिर्जित भ्रामक सामग्रीको बिगबिगी बढेपछि विज्ञहरूले त्यसबाट पर्ने प्रभावबारे चिन्ता व्यक्त गरेका छन्।', 'जबरजस्ती करणी मुद्दामा उच्च अदालत पाटनले सफाइ दिएको केही घण्टापछि नेपाल क्रिकेट सङ्घ (क्यान) को निर्णय सार्वजनिक भएको हो।', 'उत्तर अमेरिकामा यो पहिलो विश्वकप हुँदै छ भने आयोजकको हैसियतले अमेरिकाले पनि सीधै विश्वकप खेल्ने मौका पाएको छ।', 'सहकारी संस्थाका सञ्चालकहरूले सम्पत्ति ब्याङ्कमा धितो राखेर ऋण लिएको पाइएका कारण लिलामी प्रक्रियामा समस्या भएको अधिकारीहरूले बताएका छन्।', "'ब्रेकिङ'लाई ओलिम्पिक्समा पहिलो पटक समावेश गरिएको हो। यसपालि नै तालिबानको धम्कीका बीच 'ब्रेकिङ' सिकेकी मनिजा तलाश शरणार्थी टोलीकी सदस्यका रूपमा खेल्दै छिन्।"]

#     # Preprocess the data
#     cleaned_data = [preprocess_text(doc) for doc in data]
#     print(cleaned_data)

#     # Further steps, like tokenization or saving the cleaned data, can follow


In [ ]:
import pandas as pd
import math
import os

def save_to_txt_in_chunks(input_file, output_folder, max_file_size_mb=50):
    # Ensure output folder exists
    os.makedirs(output_folder, exist_ok=True)

    # Size limit for each output file in bytes
    max_file_size = max_file_size_mb * 1024 * 1024
    file_index = 1  # Track the file number
    output_file = os.path.join(output_folder, f"chunk_{file_index}.txt")

    # Read input CSV file in chunks
    chunk_size = 10000  # Number of rows per chunk
    chunk_iter = pd.read_csv(input_file, chunksize=chunk_size)

    # Open the initial output file for writing
    f_out = open(output_file, mode='w', encoding='utf-8')

    for chunk in chunk_iter:
        # Process each chunk
        chunk['processed_text'] = chunk['text'].apply(data_cleaner.clean_data)

        # Write each processed row to the output .txt file with <endoftext> token
        for row in chunk['processed_text']:
            f_out.write(f"{row} <|endoftext|>")

            # Check if the current file size exceeds the limit
            if os.path.getsize(output_file) > max_file_size:
                f_out.close()  # Close the current file
                print(f'saved file: {f_out.name}')
                file_index += 1
                output_file = os.path.join(output_folder, f"chunk_{file_index}.txt")
                f_out = open(output_file, mode='w', encoding='utf-8')  # Open a new file

    # Close the last open file
    f_out.close()

if __name__ == "__main__":
    input_csv = '/content/drive/MyDrive/Research/datasets/nepberta/dataset/clean_date_categories.csv'
    output_folder = 'nepberta/clean_date_categories'

    # Remove previous data of output folder
    if os.path.exists(output_folder):
        shutil.rmtree(output_folder)

    # Create output folder if it does not exist
    if not os.path.exists(output_folder):
        print(f'creating folder')
        os.makedirs(output_folder)

    save_to_txt_in_chunks(input_csv, output_folder, max_file_size_mb=50)



creating folder


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_1.txt


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_2.txt
saved file: nepberta/clean_date_categories/chunk_3.txt


...

saved file: nepberta/clean_date_categories/chunk_228.txt


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_229.txt


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


TypeError: object of type 'float' has no len()

In [ ]:
229*50/1024

11.181640625

In [ ]:
# # v2: Save cleaned output to a csv file
# # do not create giant string
# import pandas as pd
# import math
# import os
# import shutil

# def save_to_csv_in_chunks(input_file, output_folder, max_file_size_mb=500):
#     # Ensure output folder exists
#     os.makedirs(output_folder, exist_ok=True)

#     # Size limit for each output file in bytes
#     max_file_size = max_file_size_mb * 1024 * 1024
#     file_index = 1  # Track the file number
#     output_file = os.path.join(output_folder, f"chunk_{file_index}.csv")

#     # Read input CSV file in chunks
#     chunk_size = 10000  # Number of rows per chunk
#     chunk_iter = pd.read_csv(input_file, chunksize=chunk_size)

#     for chunk in chunk_iter:
#         # Process each chunk
#         chunk['text'] = chunk['text'].apply(data_cleaner.clean_data)

#         # Save the chunk to a new CSV file if the current file size exceeds the limit
#         while os.path.exists(output_file) and os.path.getsize(output_file) > max_file_size:
#             file_index += 1
#             output_file = os.path.join(output_folder, f"chunk_{file_index}.csv")

#         # Save processed chunk to CSV file, appending if the file already exists
#         chunk.to_csv(output_file, mode='a', index=False, encoding='utf-8', header=not os.path.exists(output_file))
#         print(f'saved file: {output_file}')

# if __name__ == "__main__":
#     input_csv = '/content/drive/MyDrive/Research/datasets/nepberta/dataset/clean_date_categories.csv'
#     output_folder = 'nepberta/clean_date_categories/'

#     # Remove previous data in output folder
#     if os.path.exists(output_folder):
#         shutil.rmtree(output_folder)

#     # Create output folder if it does not exist
#     if not os.path.exists(output_folder):
#         print(f'creating folder')
#         os.makedirs(output_folder)

#     save_to_csv_in_chunks(input_csv, output_folder, max_file_size_mb=50)


creating folder


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_1.csv


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_2.csv
saved file: nepberta/clean_date_categories/chunk_2.csv


...

<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_13.csv


<ipython-input-4-12fd7fc5839a>:22: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, "lxml")


saved file: nepberta/clean_date_categories/chunk_14.csv
saved file: nepberta/clean_date_categories/chunk_14.csv


KeyboardInterrupt: 

# Upload dataset to huggingface

In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: write).
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
from google.colab import userdata
token=userdata.get('HUGGING_FACE_BEARER')

In [ ]:
# # delete folder nepberta/ from huggingface
!huggingface-cli repo-files Aananda-giri/nepali_llm_datasets delete nepberta/ --repo-type dataset

Files correctly deleted from repo. Commit: https://huggingface.co/datasets/Aananda-giri/nepali_llm_datasets/commit/6b26d5cc1ac9c83aa526bd7c33010393802c93aa.


In [ ]:
# Upload to Hugging Face
from huggingface_hub import HfApi, Repository
import os
import shutil

# Set your dataset repo name and Hugging Face username
username = "Aananda-giri"  # Replace with your Hugging Face username
repo_name = "nepali_llm_datasets"  # Name for the new dataset repository
repo_id = f"{username}/{repo_name}"  # Full repository ID

# Authenticate
api = HfApi()
# token = "token"  # Replace with your Hugging Face token

# Local dataset directory
local_dir = "./"  # Adjust to the path of the dataset folder

# Create the repository if it does not exist
api.create_repo(repo_id, token=token, repo_type="dataset", exist_ok=True)

# # Clone the repo from Hugging Face Hub if it does not already exist locally
# repo = Repository(
#     local_dir=local_dir,
#     clone_from=repo_id,  # Use `clone_from` to set up repository cloning
#     token=token,
#     repo_type="dataset"
# )

# # Add all files and folders to the Git repository
# repo.git_add(".")  # Stage all files
# repo.git_commit("Add all dataset files and folders")  # Commit the changes

# # Push the current structure to the Hugging Face Hub
# repo.push_to_hub(commit_message="Initial upload of structured Nepali LLM dataset folders")

# print(f"Dataset uploaded to https://huggingface.co/datasets/{repo_id}")


RepoUrl('https://huggingface.co/datasets/Aananda-giri/nepali_llm_datasets', endpoint='https://huggingface.co', repo_type='dataset', repo_id='Aananda-giri/nepali_llm_datasets')

In [ ]:
# !git lfs track nepberta/clean_date_categories

Tracking "nepberta/clean_date_categories"


In [ ]:
# # Add and commit the files
# !git add .
# !git commit -m "Add large dataset files with Git LFS"
# !git push origin main

fatal: cannot exec '.git/hooks/post-commit': Permission denied
[main 3e99b97] Add large dataset files with Git LFS
 2 files changed, 2 insertions(+), 1 deletion(-)
fatal: cannot exec '.git/hooks/pre-push': Permission denied
^C


In [ ]:
# Local dataset directory
local_dir = "./"  # Path to your dataset folder

# Upload all files and folders recursively
for root, dirs, files in os.walk(local_dir):
    for file in files:
        file_path = os.path.join(root, file)
        # Upload file to the specified repo with the same directory structure
        repo_file_path = os.path.relpath(file_path, local_dir)
        if 'chunk_' in repo_file_path:
            chunk_id = int(repo_file_path.split('.txt')[0].split('chunk_')[-1])
            # if chunk_id <= 124:
            #   # have uploaded up to chunk_124.txt before rate limit
            #   continue
        api.upload_file(
            path_or_fileobj=file_path,
            path_in_repo=repo_file_path,
            repo_id=repo_id,
            repo_type="dataset",
            token=token
        )

print(f"Dataset uploaded to https://huggingface.co/datasets/{repo_id}")

No files have been modified since last commit. Skipping to prevent empty commit.
No files have been modified since last commit. Skipping to prevent empty commit.


chunk_126.txt:   0%|          | 0.00/52.5M [00:00<?, ?B/s]

chunk_127.txt:   0%|          | 0.00/52.4M [00:00<?, ?B/s]

chunk_128.txt:   0%|          | 0.00/52.4M [00:00<?, ?B/s]

chunk_129.txt:   0%|          | 0.00/52.5M [00:00<?, ?B/s]

...

chunk_227.txt:   0%|          | 0.00/52.5M [00:00<?, ?B/s]

chunk_228.txt:   0%|          | 0.00/52.4M [00:00<?, ?B/s]

chunk_229.txt:   0%|          | 0.00/52.5M [00:00<?, ?B/s]

chunk_230.txt:   0%|          | 0.00/15.3M [00:00<?, ?B/s]

ValueError: Invalid `path_in_repo` in CommitOperation: cannot update files under a '.git/' folder (path: '.git/description').

# Scrapy Engine

In [ ]:
%cd /content/drive/MyDrive/Research/datasets/hf_datasets

/content/drive/MyDrive/Research/datasets/hf_datasets


In [ ]:
import os;
os.makedirs('scrapy_engine', exist_ok=True)
local_dir='scrapy_engine'

In [ ]:
# Upload to Hugging Face
from huggingface_hub import HfApi, Repository
import os
import shutil

# Set your dataset repo name and Hugging Face username
username = "Aananda-giri"  # Replace with your Hugging Face username
repo_name = "nepali_llm_datasets"  # Name for the new dataset repository
repo_id = f"{username}/{repo_name}"  # Full repository ID

# Authenticate
api = HfApi()
# token = "token"  # Replace with your Hugging Face token

# Create the repository if it does not exist
api.create_repo(repo_id, token=token, repo_type="dataset", exist_ok=True)

In [ ]:
!ls

nepberta  preprocess.ipynb  scrapy_engine


In [ ]:
!ls

nepberta  preprocess.ipynb  scrapy_engine


In [ ]:
# copy files from ../scrapy_engine to ./scrapy_engine
import shutil
files_to_upload = ['cleaned_data.csv']
folders_to_upload = ['code']
# Upload all files and folders recursively
for root, dirs, files in os.walk('../scrapy_engine'):

    for file in files:
        # print(file)
        if file in files_to_upload or True in [root.endswith(folder) for folder in folders_to_upload]:
          file_path = os.path.join(root, file)
          shutil.copy(file_path, './scrapy_engine')
          print(root, file_path)

../scrapy_engine ../scrapy_engine/cleaned_data.csv
../scrapy_engine/code ../scrapy_engine/code/load_data.py
../scrapy_engine/code ../scrapy_engine/code/2. pre-process.ipynb
../scrapy_engine/code ../scrapy_engine/code/0. load_data.ipynb
../scrapy_engine/code ../scrapy_engine/code/1. merge-data.ipynb


In [ ]:
local_dir= './'
# Upload all files and folders recursively
for root, dirs, files in os.walk(local_dir):
    if root.endswith('scrapy_engine'):
      for file in files:
          file_path = os.path.join(root, file)
          # Upload file to the specified repo with the same directory structure
          repo_file_path = os.path.relpath(file_path, local_dir)
          api.upload_file(
              path_or_fileobj=file_path,
              path_in_repo=repo_file_path,
              repo_id=repo_id,
              repo_type="dataset",
              token=token
          )

print(f"Dataset uploaded to https://huggingface.co/datasets/{repo_id}")

KeyboardInterrupt: 

In [ ]:
# # List of files to delete
# files_to_delete = [
#     "cleaned_data.csv",
#     "load_data.py",
#     "2. pre-process.ipynb",
#     "0. load_data.ipynb",
#     "1. merge-data.ipynb"
# ]

# # Delete each file
# for file_path in files_to_delete:
#     api.delete_file(
#         path_in_repo=file_path,
#         repo_id=repo_id,
#         repo_type="dataset",
#         token=token
#     )

# README
* config-structure: https://huggingface.co/docs/datasets/en/repository_structure

* upload single file: https://huggingface.co/docs/datasets/en/share


In [ ]:
# 80% for training and 20% for testing
import os
import yaml

# Path to the directory containing the .txt files
data_dir = "nepberta/clean_date_categories/"
files = sorted([f for f in os.listdir(data_dir) if f.endswith('.txt')])

# Calculate split sizes (80% for training, 20% for testing)
train_size = int(0.8 * len(files))

# Split the files into train and test
train_files = files[:train_size]
test_files = files[train_size:]

# Create the configuration
config = {
    "configs": [
        {
            "config_name": "nepberta",
            "data_files": [

                {
                    "split": "test",
                    "path": [os.path.join(data_dir, f) for f in test_files]
                }
            ]
        }
    ]
}

# print(config)
# # Print or save the config
import yaml
print(yaml.dump(config))

# # Save the config to a text file
# with open("dataset_config.yaml", "w") as file:
#     yaml.dump(config, file)

# print("Configuration saved to dataset_config.yaml")

In [1]:
%%writefile README.md
---
configs:
- config_name: nepberta
  data_files:
  - split: train
    path:
    - nepberta/clean_date_categories/chunk_1.txt
    - nepberta/clean_date_categories/chunk_10.txt
    - nepberta/clean_date_categories/chunk_100.txt
    - nepberta/clean_date_categories/chunk_101.txt
    - nepberta/clean_date_categories/chunk_102.txt
    - nepberta/clean_date_categories/chunk_103.txt
    - nepberta/clean_date_categories/chunk_104.txt
    - nepberta/clean_date_categories/chunk_105.txt
    - nepberta/clean_date_categories/chunk_106.txt
    - nepberta/clean_date_categories/chunk_107.txt
    - nepberta/clean_date_categories/chunk_108.txt
    - nepberta/clean_date_categories/chunk_109.txt
    - nepberta/clean_date_categories/chunk_11.txt
    - nepberta/clean_date_categories/chunk_110.txt
    - nepberta/clean_date_categories/chunk_111.txt
    - nepberta/clean_date_categories/chunk_112.txt
    - nepberta/clean_date_categories/chunk_113.txt
    - nepberta/clean_date_categories/chunk_114.txt
    - nepberta/clean_date_categories/chunk_115.txt
    - nepberta/clean_date_categories/chunk_116.txt
    - nepberta/clean_date_categories/chunk_117.txt
    - nepberta/clean_date_categories/chunk_118.txt
    - nepberta/clean_date_categories/chunk_119.txt
    - nepberta/clean_date_categories/chunk_12.txt
    - nepberta/clean_date_categories/chunk_120.txt
    - nepberta/clean_date_categories/chunk_121.txt
    - nepberta/clean_date_categories/chunk_122.txt
    - nepberta/clean_date_categories/chunk_123.txt
    - nepberta/clean_date_categories/chunk_124.txt
    - nepberta/clean_date_categories/chunk_125.txt
    - nepberta/clean_date_categories/chunk_126.txt
    - nepberta/clean_date_categories/chunk_127.txt
    - nepberta/clean_date_categories/chunk_128.txt
    - nepberta/clean_date_categories/chunk_129.txt
    - nepberta/clean_date_categories/chunk_13.txt
    - nepberta/clean_date_categories/chunk_130.txt
    - nepberta/clean_date_categories/chunk_131.txt
    - nepberta/clean_date_categories/chunk_132.txt
    - nepberta/clean_date_categories/chunk_133.txt
    - nepberta/clean_date_categories/chunk_134.txt
    - nepberta/clean_date_categories/chunk_135.txt
    - nepberta/clean_date_categories/chunk_136.txt
    - nepberta/clean_date_categories/chunk_137.txt
    - nepberta/clean_date_categories/chunk_138.txt
    - nepberta/clean_date_categories/chunk_139.txt
    - nepberta/clean_date_categories/chunk_14.txt
    - nepberta/clean_date_categories/chunk_140.txt
    - nepberta/clean_date_categories/chunk_141.txt
    - nepberta/clean_date_categories/chunk_142.txt
    - nepberta/clean_date_categories/chunk_143.txt
    - nepberta/clean_date_categories/chunk_144.txt
    - nepberta/clean_date_categories/chunk_145.txt
    - nepberta/clean_date_categories/chunk_146.txt
    - nepberta/clean_date_categories/chunk_147.txt
    - nepberta/clean_date_categories/chunk_148.txt
    - nepberta/clean_date_categories/chunk_149.txt
    - nepberta/clean_date_categories/chunk_15.txt
    - nepberta/clean_date_categories/chunk_150.txt
    - nepberta/clean_date_categories/chunk_151.txt
    - nepberta/clean_date_categories/chunk_152.txt
    - nepberta/clean_date_categories/chunk_153.txt
    - nepberta/clean_date_categories/chunk_154.txt
    - nepberta/clean_date_categories/chunk_155.txt
    - nepberta/clean_date_categories/chunk_156.txt
    - nepberta/clean_date_categories/chunk_157.txt
    - nepberta/clean_date_categories/chunk_158.txt
    - nepberta/clean_date_categories/chunk_159.txt
    - nepberta/clean_date_categories/chunk_16.txt
    - nepberta/clean_date_categories/chunk_160.txt
    - nepberta/clean_date_categories/chunk_161.txt
    - nepberta/clean_date_categories/chunk_162.txt
    - nepberta/clean_date_categories/chunk_163.txt
    - nepberta/clean_date_categories/chunk_164.txt
    - nepberta/clean_date_categories/chunk_165.txt
    - nepberta/clean_date_categories/chunk_166.txt
    - nepberta/clean_date_categories/chunk_167.txt
    - nepberta/clean_date_categories/chunk_168.txt
    - nepberta/clean_date_categories/chunk_169.txt
    - nepberta/clean_date_categories/chunk_17.txt
    - nepberta/clean_date_categories/chunk_170.txt
    - nepberta/clean_date_categories/chunk_171.txt
    - nepberta/clean_date_categories/chunk_172.txt
    - nepberta/clean_date_categories/chunk_173.txt
    - nepberta/clean_date_categories/chunk_174.txt
    - nepberta/clean_date_categories/chunk_175.txt
    - nepberta/clean_date_categories/chunk_176.txt
    - nepberta/clean_date_categories/chunk_177.txt
    - nepberta/clean_date_categories/chunk_178.txt
    - nepberta/clean_date_categories/chunk_179.txt
    - nepberta/clean_date_categories/chunk_18.txt
    - nepberta/clean_date_categories/chunk_180.txt
    - nepberta/clean_date_categories/chunk_181.txt
    - nepberta/clean_date_categories/chunk_182.txt
    - nepberta/clean_date_categories/chunk_183.txt
    - nepberta/clean_date_categories/chunk_184.txt
    - nepberta/clean_date_categories/chunk_185.txt
    - nepberta/clean_date_categories/chunk_186.txt
    - nepberta/clean_date_categories/chunk_187.txt
    - nepberta/clean_date_categories/chunk_188.txt
    - nepberta/clean_date_categories/chunk_189.txt
    - nepberta/clean_date_categories/chunk_19.txt
    - nepberta/clean_date_categories/chunk_190.txt
    - nepberta/clean_date_categories/chunk_191.txt
    - nepberta/clean_date_categories/chunk_192.txt
    - nepberta/clean_date_categories/chunk_193.txt
    - nepberta/clean_date_categories/chunk_194.txt
    - nepberta/clean_date_categories/chunk_195.txt
    - nepberta/clean_date_categories/chunk_196.txt
    - nepberta/clean_date_categories/chunk_197.txt
    - nepberta/clean_date_categories/chunk_198.txt
    - nepberta/clean_date_categories/chunk_199.txt
    - nepberta/clean_date_categories/chunk_2.txt
    - nepberta/clean_date_categories/chunk_20.txt
    - nepberta/clean_date_categories/chunk_200.txt
    - nepberta/clean_date_categories/chunk_201.txt
    - nepberta/clean_date_categories/chunk_202.txt
    - nepberta/clean_date_categories/chunk_203.txt
    - nepberta/clean_date_categories/chunk_204.txt
    - nepberta/clean_date_categories/chunk_205.txt
    - nepberta/clean_date_categories/chunk_206.txt
    - nepberta/clean_date_categories/chunk_207.txt
    - nepberta/clean_date_categories/chunk_208.txt
    - nepberta/clean_date_categories/chunk_209.txt
    - nepberta/clean_date_categories/chunk_21.txt
    - nepberta/clean_date_categories/chunk_210.txt
    - nepberta/clean_date_categories/chunk_211.txt
    - nepberta/clean_date_categories/chunk_212.txt
    - nepberta/clean_date_categories/chunk_213.txt
    - nepberta/clean_date_categories/chunk_214.txt
    - nepberta/clean_date_categories/chunk_215.txt
    - nepberta/clean_date_categories/chunk_216.txt
    - nepberta/clean_date_categories/chunk_217.txt
    - nepberta/clean_date_categories/chunk_218.txt
    - nepberta/clean_date_categories/chunk_219.txt
    - nepberta/clean_date_categories/chunk_22.txt
    - nepberta/clean_date_categories/chunk_220.txt
    - nepberta/clean_date_categories/chunk_221.txt
    - nepberta/clean_date_categories/chunk_222.txt
    - nepberta/clean_date_categories/chunk_223.txt
    - nepberta/clean_date_categories/chunk_224.txt
    - nepberta/clean_date_categories/chunk_225.txt
    - nepberta/clean_date_categories/chunk_226.txt
    - nepberta/clean_date_categories/chunk_227.txt
    - nepberta/clean_date_categories/chunk_228.txt
    - nepberta/clean_date_categories/chunk_229.txt
    - nepberta/clean_date_categories/chunk_23.txt
    - nepberta/clean_date_categories/chunk_230.txt
    - nepberta/clean_date_categories/chunk_24.txt
    - nepberta/clean_date_categories/chunk_25.txt
    - nepberta/clean_date_categories/chunk_26.txt
    - nepberta/clean_date_categories/chunk_27.txt
    - nepberta/clean_date_categories/chunk_28.txt
    - nepberta/clean_date_categories/chunk_29.txt
    - nepberta/clean_date_categories/chunk_3.txt
    - nepberta/clean_date_categories/chunk_30.txt
    - nepberta/clean_date_categories/chunk_31.txt
    - nepberta/clean_date_categories/chunk_32.txt
    - nepberta/clean_date_categories/chunk_33.txt
    - nepberta/clean_date_categories/chunk_34.txt
    - nepberta/clean_date_categories/chunk_35.txt
    - nepberta/clean_date_categories/chunk_36.txt
    - nepberta/clean_date_categories/chunk_37.txt
    - nepberta/clean_date_categories/chunk_38.txt
    - nepberta/clean_date_categories/chunk_39.txt
    - nepberta/clean_date_categories/chunk_4.txt
    - nepberta/clean_date_categories/chunk_40.txt
    - nepberta/clean_date_categories/chunk_41.txt
    - nepberta/clean_date_categories/chunk_42.txt
    - nepberta/clean_date_categories/chunk_43.txt
    - nepberta/clean_date_categories/chunk_44.txt
    - nepberta/clean_date_categories/chunk_45.txt
    - nepberta/clean_date_categories/chunk_46.txt
    - nepberta/clean_date_categories/chunk_47.txt
    - nepberta/clean_date_categories/chunk_48.txt
    - nepberta/clean_date_categories/chunk_49.txt
    - nepberta/clean_date_categories/chunk_5.txt
    - nepberta/clean_date_categories/chunk_50.txt
    - nepberta/clean_date_categories/chunk_51.txt
    - nepberta/clean_date_categories/chunk_52.txt
    - nepberta/clean_date_categories/chunk_53.txt
    - nepberta/clean_date_categories/chunk_54.txt
    - nepberta/clean_date_categories/chunk_55.txt
    - nepberta/clean_date_categories/chunk_56.txt
    - nepberta/clean_date_categories/chunk_57.txt
  - split: test
    path:
    - nepberta/clean_date_categories/chunk_58.txt
    - nepberta/clean_date_categories/chunk_59.txt
    - nepberta/clean_date_categories/chunk_6.txt
    - nepberta/clean_date_categories/chunk_60.txt
    - nepberta/clean_date_categories/chunk_61.txt
    - nepberta/clean_date_categories/chunk_62.txt
    - nepberta/clean_date_categories/chunk_63.txt
    - nepberta/clean_date_categories/chunk_64.txt
    - nepberta/clean_date_categories/chunk_65.txt
    - nepberta/clean_date_categories/chunk_66.txt
    - nepberta/clean_date_categories/chunk_67.txt
    - nepberta/clean_date_categories/chunk_68.txt
    - nepberta/clean_date_categories/chunk_69.txt
    - nepberta/clean_date_categories/chunk_7.txt
    - nepberta/clean_date_categories/chunk_70.txt
    - nepberta/clean_date_categories/chunk_71.txt
    - nepberta/clean_date_categories/chunk_72.txt
    - nepberta/clean_date_categories/chunk_73.txt
    - nepberta/clean_date_categories/chunk_74.txt
    - nepberta/clean_date_categories/chunk_75.txt
    - nepberta/clean_date_categories/chunk_76.txt
    - nepberta/clean_date_categories/chunk_77.txt
    - nepberta/clean_date_categories/chunk_78.txt
    - nepberta/clean_date_categories/chunk_79.txt
    - nepberta/clean_date_categories/chunk_8.txt
    - nepberta/clean_date_categories/chunk_80.txt
    - nepberta/clean_date_categories/chunk_81.txt
    - nepberta/clean_date_categories/chunk_82.txt
    - nepberta/clean_date_categories/chunk_83.txt
    - nepberta/clean_date_categories/chunk_84.txt
    - nepberta/clean_date_categories/chunk_85.txt
    - nepberta/clean_date_categories/chunk_86.txt
    - nepberta/clean_date_categories/chunk_87.txt
    - nepberta/clean_date_categories/chunk_88.txt
    - nepberta/clean_date_categories/chunk_89.txt
    - nepberta/clean_date_categories/chunk_9.txt
    - nepberta/clean_date_categories/chunk_90.txt
    - nepberta/clean_date_categories/chunk_91.txt
    - nepberta/clean_date_categories/chunk_92.txt
    - nepberta/clean_date_categories/chunk_93.txt
    - nepberta/clean_date_categories/chunk_94.txt
    - nepberta/clean_date_categories/chunk_95.txt
    - nepberta/clean_date_categories/chunk_96.txt
    - nepberta/clean_date_categories/chunk_97.txt
    - nepberta/clean_date_categories/chunk_98.txt
    - nepberta/clean_date_categories/chunk_99.txt
- config_name: scrapy_engine
  data_files:
  - split: train
    path:
      - "scrapy_engine/cleaned_data.csv"
---
# Nepali LLM Datasets

This repository contains two configurations of Nepali LLM datasets:

## Configurations

### 1. Scrapy Engine
- Description: Contains data collected using a web scraping engine.
- Files: [List any specific files or formats]

### 2. Nepberta
- Description: This dataset is derived from the Nepberta project and contains cleaned data specifically related to the project. The dataset contains **cleaned text chunks of size ~50 mb ** of all articles into a single giant string, with each article ending in <|endoftext|>. This long string is then segmented into chunks, each approximately 500 MB in size.
- Files: contains 23 files each ~500Mb (chunk_1.txt, chunk_2.txt, ... chunk_23.txt)
- split:train
  * files: chunk_1.txt to chunk_18.txt
- split:test
  * files: chunk_19.txt to chunk_23.txt

## Usage

To load the datasets:

```python
# it loads entire dataset first
from datasets import load_dataset

# Load nepberta configuration
nepberta_dataset = load_dataset("Aananda-giri/nepali_llm_datasets", name="nepberta", split='train') # use `streaming=True` to avoid downloading all the dataset

# length of chunks
len(nepberta_train['text']) # 18 : number of chunks
len(nepberta_train['text'][0])  # length of large text equivalent to 500 MB text

# use streaming=True to avoid downloading entire dataset
nepberta_train = load_dataset("Aananda-giri/nepali_llm_datasets", name="nepberta", streaming=True)['train']

# using next
next(iter(nepberta_train))

# using for loop
for large_chunk in nepberta_train:
  pass
  # code to process large_chunk['text']

# Load scrapy engine data
scrapy_train = load_dataset("Aananda-giri/nepali_llm_datasets", name="scrapy_engine" split="train")
```

Writing README.md


In [2]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) 
Token is valid (permission: write).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in c

In [3]:
!huggingface-cli upload Aananda-giri/nepali_llm_datasets README.md --repo-type dataset

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
https://huggingface.co/datasets/Aananda-giri/nepali_llm_datasets/blob/main/README.md


In [ ]:
!ls

nepberta  preprocess.ipynb  README.md  scrapy_engine


# Create new smaller dataset with only 3 500Mb chunks

In [ ]:
!pip install datasets --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 12.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.8 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) 
Token is valid (permission: write).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in c

In [ ]:
from datasets import load_dataset

# Load only three chunks from the streaming dataset
nepberta_train_stream = load_dataset("Aananda-giri/nepali_llm_datasets", "nepberta", streaming=True)["train"]

target_dir = 'nepberta_sample'
import os; os.mkdir(target_dir)

# Save each chunk to a separate text file
for i in range(3):
    chunk = next(iter(nepberta_train_stream))  # Get the next chunk
    with open(os.path.join(target_dir, f"combined_{i+1}.txt"), "w", encoding="utf-8") as file:
        file.write(chunk['text'])
    print(f"Saved chunk {i+1} to chunk_{i+1}.txt")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/3.12k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/18 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/18 [00:00<?, ?it/s]

Saved chunk 1 to chunk_1.txt
Saved chunk 2 to chunk_2.txt
Saved chunk 3 to chunk_3.txt


In [ ]:
from datasets import Dataset, DatasetDict, load_dataset

# Load the text files as a dataset
new_dataset = load_dataset("text", data_files="nepberta_sample/*.txt", split="train")

# Wrap in a DatasetDict for compatibility with push_to_hub
new_dataset_dict = DatasetDict({"train": new_dataset})

# Push to Hugging Face Hub
new_dataset_dict.push_to_hub("Aananda-giri/nepberta-sample")

In [ ]:
!huggingface-cli upload Aananda-giri/nepberta-sample ./nepberta_sample . --repo-type dataset

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
combined_3.txt:   0% 0.00/524M [00:00<?, ?B/s]
Upload 3 LFS files:   0% 0/3 [00:00<?, ?it/s]

combined_3.txt:   0% 0.00/524M [00:00<?, ?B/s]


combined_3.txt:   0% 98.3k/524M [00:00<10:03, 869kB/s]

combined_3.txt:   0% 606k/524M [00:00<01:33, 5.59MB/s]


combined_3.txt:   0% 344k/524M [00:00<02:47, 3.13MB/s]

combined_3.txt:   2% 9.34M/524M [00:00<00:10, 47.9MB/s]


combined_3.txt:   1% 3.39M/524M [00:00<00:35, 14.5MB/s]


combined_3.txt:   1% 5.65M/524M [00:00<00:31, 16.2MB/s]

combined_3.txt:   2% 10.0M/524M [00:00<00:21, 24.4MB/s]


combined_3.txt:   3% 16.0M/524M [00:00<00:18, 27.9MB/s]

combined_3.txt:   3% 13.7M/524M [00:00<00:18, 27.3MB/s]


combined_3.txt:   4% 22.4M/524M [00:00<00:14, 34.4MB/s]


combined_3.txt:   3% 16.5M/524M [00:00<00:27, 18.7MB/s]

combined_3.txt:   4% 22.5M/524M [00:00<00:17, 27.9MB/s]



In [ ]:
%%writefile README.md
# Nepali Text Dataset (Sampled Chunks)

This repository contains a sample of the Nepali text dataset, with three 500MB cleaned chunks from the larger `nepberta` dataset. The dataset is ideal for experimenting with language modeling, NLP, and machine learning projects involving Nepali text.

## Dataset Overview
The dataset consists of Nepali text data, specifically sampled to provide a representative subset without requiring the full dataset size. Each chunk contains approximately 500MB of Nepali text data, providing ample content for model training or evaluation purposes.

### Structure
The dataset is structured as follows:
- **Train split**: Three chunks, each approximately 500MB in size.

### Dataset Details
- **Language**: Nepali
- **Source**: [Original Dataset](https://huggingface.co/datasets/Aananda-giri/nepali_llm_datasets)
- **Dataset Size**: 1.5GB (3 chunks, each 500MB)

## Usage

To load the dataset in your projects, you can use the Hugging Face `datasets` library as follows:

```python
from datasets import load_dataset

# Load the dataset from the Hugging Face Hub
sampled_dataset = load_dataset("your-username/your-new-dataset-name", split="train")

# Inspect the first sample
print(len(sampled_dataset[0]))
```

### Save only 1 out of three chunks
```python
from datasets import load_dataset

num_chunks_to_save = 1

# Load the dataset from the Hugging Face Hub
sampled_dataset_stream = load_dataset("Aananda-giri/nepberta-sample", split="train", streaming=True)

target_dir = 'nepberta_sample'

import os
if not os.path.exists(target_dir):
  os.mkdir(target_dir)

# Save each chunk to a separate text file
for i in range(num_chunks_to_save):
    chunk = next(iter(sampled_dataset_stream))  # Get the next chunk
    with open(os.path.join(target_dir, f"combined_{i+1}.txt"), "w", encoding="utf-8") as file:
        file.write(chunk['text'])
    print(f"Saved chunk {i+1} to chunk_{i+1}.txt")
```

Example Code for Loading Chunks
This example code demonstrates how to iterate through the chunks and process them as needed:


```
for chunk in sampled_dataset:
    text_data = chunk["text"]
    # Process or analyze text_data as needed
```

## Intended Use
This dataset is suitable for:

* Experimenting on smaller model before training larger model
* Research and development in language processing tasks
* Experimenting with large language models on Nepali text data

Writing README.md


In [ ]:
from datasets import load_dataset

num_chunks_to_save = 1

# Load the dataset from the Hugging Face Hub
sampled_dataset_stream = load_dataset("Aananda-giri/nepberta-sample", split="train", streaming=True)

target_dir = 'nepberta_sample'

import os
if not os.path.exists(target_dir):
  os.mkdir(target_dir)

# Save each chunk to a separate text file
for i in range(num_chunks_to_save):
    chunk = next(iter(sampled_dataset_stream))  # Get the next chunk
    with open(os.path.join(target_dir, f"combined_{i+1}.txt"), "w", encoding="utf-8") as file:
        file.write(chunk['text'])
    print(f"Saved chunk {i+1} to chunk_{i+1}.txt")

Repo card metadata block was not found. Setting CardData to empty.


Saved chunk 1 to chunk_1.txt


In [ ]:
!huggingface-cli upload Aananda-giri/nepberta-sample README.md --repo-type dataset

Consider using `hf_transfer` for faster uploads. This solution comes with some limitations. See https://huggingface.co/docs/huggingface_hub/hf_transfer for more details.
/usr/local/lib/python3.10/dist-packages/huggingface_hub/hf_api.py:3757: UserWarning: Warnings while validating metadata in README.md:
- empty or missing yaml metadata in repo card
  warnings.warn(f"Warnings while validating metadata in README.md:\n{message}")
https://huggingface.co/datasets/Aananda-giri/nepberta-sample/blob/main/README.md
